In [1]:
import pandas as pd
import numpy as np 
import glob
import os 
from openpyxl import load_workbook
from openpyxl.styles import PatternFill, Font
from datetime import datetime

In [2]:
hoje = datetime.today().strftime('%Y-%m-%d')

In [3]:
#precisa ver duplicidade de desc e vendas irece.

In [4]:
df_tabela = pd.read_excel(r"C:\Users\joao.herculano\GRUPO GINSENG\Assistência Suprimentos - 2025\SUPRIMENTOS\DB_PROMOÇÕES\QDB\BW\tabela de pedido\Pedidos Semanais Especiais - QDB - 202513.xlsx")

df_tabela = df_tabela[df_tabela['Ação revendedor'].notna() | df_tabela['Ação consumidor'].notna()]

df_tabela = df_tabela[df_tabela['Região'] == 'NNE'] 

df_tabela = df_tabela[(df_tabela['Canal'] != 'Ecomm')]

#df_tabela['Canal'] = np.where((df_tabela['Canal'] == "Loja") | (df_tabela['Canal'] == "Todos") | (df_tabela['Canal'] == "Loja | VD"),"TODOS","VD")

df_tabela = df_tabela[(df_tabela['Categoria'] != "EMBALAGENS") | (df_tabela['Categoria'] != "SUPORTE À VENDA")]

#df_tabela = df_tabela[df_tabela['Tipo de pedido'] == 'Semanal']

df_tabela = df_tabela[~df_tabela['Descrição'].str.contains('PRM')]

#df_tabela = df_tabela[df_tabela['Tipo de produto']!= 'EDICAO LIMITADA']

df_tabela['Ação revendedor'] = np.where(df_tabela['Ação revendedor'].isna(),df_tabela['Ação consumidor'],df_tabela['Ação revendedor'])

df_tabela['Percentual de desconto revendedor'] = np.where(df_tabela['Percentual de desconto revendedor'].isna(),df_tabela['Percentual de desconto consumidor'],df_tabela['Percentual de desconto revendedor'])

df_tabela['MATCH'] = 1



In [5]:
df_tabela['Código'].value_counts()

Código
47196    1
49901    1
49909    1
53958    1
51021    1
        ..
79483    1
51890    1
56323    1
56324    1
56321    1
Name: count, Length: 108, dtype: int64

In [6]:
df_tabela.head()

Ciclo Região  Canal  Código                           Descrição  IAF  \
0  202513    NNE  Todos   47196     QDB MASC CILIO BIG BANG 360 10g  Não   
1  202513    NNE  Todos   49901                   QDB PINCEL SOMBRA  Não   
2  202513    NNE  Todos   49909  QDB PINCEL SUPERACAB PELE PERFEITA  Não   
3  202513    NNE  Todos   53958           QDB MALETA MAQUIAGEM G PU  Não   
4  202513    NNE  Todos   51021         QDB BLUSH LIQ GUARANA 6,8ml  Não   

  Tipo de pedido Foco Unidade de negócio                Marca  ... Catálogo  \
0       Especial  Sim                QDB  QUEM DISSE BERENICE  ...      Sim   
1        Semanal  Não                QDB  QUEM DISSE BERENICE  ...      Sim   
2        Semanal  Não                QDB  QUEM DISSE BERENICE  ...      Sim   
3        Semanal  Não                QDB  QUEM DISSE BERENICE  ...      Não   
4       Especial  Sim                QDB  QUEM DISSE BERENICE  ...      Sim   

   Tipo de produto                                    Ação consumidor  \
0          REGULAR  [QDB - LOJA/ECOMM] BEAUTY WEEK - ISCAS ESTRATÉ...   
1          REGULAR  [QDB - LOJA/ECOMM] BEAUTY WEEK - ISCAS ESTRATÉ...   
2          REGULAR  [QDB - LOJA/ECOMM] BEAUTY WEEK - ISCAS ESTRATÉ...   
3          REGULAR  [QDB - LOJA/ECOMM] BEAUTY WEEK - ISCAS EXAUSTÃ...   
4  EDICAO LIMITADA  [QDB - LOJA/ECOMM] BEAUTY WEEK - ISCAS EXAUSTÃ...   

  Percentual de desconto consumidor  \
0                             50,71   
1                     30,30 | 51,28   
2                             30,70   
3                     25,00 | 30,01   
4                             51,22   

                                     Ação revendedor  \
0     VD - FAVORITOS PARA INÍCIOS BIG BANG 360 - C13   
1  [QDB - LOJA/ECOMM] BEAUTY WEEK - ISCAS ESTRATÉ...   
2  [QDB - LOJA/ECOMM] BEAUTY WEEK - ISCAS ESTRATÉ...   
3  [QDB - LOJA/ECOMM] BEAUTY WEEK - ISCAS EXAUSTÃ...   
4  [QDB - LOJA/ECOMM] BEAUTY WEEK - ISCAS EXAUSTÃ...   

  Percentual de desconto revendedor Sortimento P Sortimento M Sortimento G  \
0                             35,00      Sortido      Sortido      Sortido   
1                              0,00      Sortido      Sortido      Sortido   
2                              0,00      Sortido      Sortido      Sortido   
3                              0,00      Sortido      Sortido      Sortido   
4                              0,00      Sortido      Sortido      Sortido   

  MATCH  
0     1  
1     1  
2     1  
3     1  
4     1  

[5 rows x 24 columns]

In [7]:
import pyodbc
import configparser

#query de vendas por ciclo

config = configparser.ConfigParser()
config.read(r"C:\Users\joao.herculano\Documents\Enviador de email\credenciais.ini")

conn = pyodbc.connect(
    f"DRIVER={{SQL Server}};"
    f"SERVER={config['banco']['host']},1433;"
    f"DATABASE=GINSENG;"
    f"UID={config['banco']['user']};"
    f"PWD={config['banco']['password']}"
)

query = f'''
SELECT 
    B.PDV, 
    B.SKU,
    bd.SKU2, 
    COALESCE(bd.SKU2, b.SKU) AS SKU_FINAL,
    B.DESCRICAO,
    SUM(CAST(b.VENDAS AS DECIMAL(18,2))) AS VENDAS_CICLO,
    C.Ciclo
FROM base_vendas_bi b
INNER JOIN ciclos_data_2025 c 
    ON CAST(b.[DATA] AS DATE) = CONVERT(DATE, c.[Date], 103) AND C.MARCA = 'QDB'
LEFT JOIN base_depara bd on b.SKU = bd.SKU 
WHERE CAST(b.[DATA] AS DATE) >= DATEADD(YEAR, -1, GETDATE())
GROUP BY
    B.PDV, 
    B.SKU,
    bd.SKU2,
    B.DESCRICAO,
    C.Ciclo
HAVING SUM(CAST(b.VENDAS AS DECIMAL(18,2))) > 0
'''
dfi = pd.read_sql(query, conn)
conn.close()

C:\Users\joao.herculano\AppData\Local\Temp\ipykernel_43676\3661949602.py:39: UserWarning: pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.
  dfi = pd.read_sql(query, conn)


In [8]:
dfi['SKU2'] = dfi['SKU2'].fillna("-")

In [9]:
dfi = dfi[dfi['SKU2'] == "-"]

dfi.head()

PDV    SKU SKU2  SKU_FINAL                                 DESCRICAO  \
0   3546  47960    -      47960  BOTI SUN PROT CPO SPR ACQ/FL FPS50 180ml   
1  20995  49680    -      49680     LILY DES COL LEAU DE LILY SOLEIL 75ml   
2  24253  19734    -      19734              THATY DES COL BOTICOLL 100ML   
4  20998  49218    -      49218            MAKE B ESTJ PO COMP HYALURONIC   
7  14668  51129    -      51129           CBEM DES ANTIT AER NUVEM V3 75g   

   VENDAS_CICLO    Ciclo  
0           5.0  C202413  
1         356.0  C202413  
2           5.0  C202508  
4           3.0  C202505  
7           5.0  C202508

In [10]:

# 1. Agrupamento
df_agrupado = dfi.groupby(['PDV', 'SKU_FINAL', 'DESCRICAO', 'Ciclo'], as_index=False)['VENDAS_CICLO'].sum()

# 2. Pivotar o DataFrame
df_pivotado = df_agrupado.pivot_table(
    index=['PDV', 'SKU_FINAL', 'DESCRICAO'],
    columns='Ciclo',
    values='VENDAS_CICLO',
    fill_value=0  # Substitui NaN por 0
)

# 3. Resetar o índice para deixar como DataFrame normal (opcional)
df_pivotadowawa = df_pivotado.reset_index()

# 4. (Opcional) Renomear colunas com prefixo "Ciclo_"
df_pivotadowawa.columns.name = None
df_pivotadowawa = df_pivotadowawa.rename(columns=lambda x: f'Ciclo_{x}' if isinstance(x, (int, str)) and str(x).isdigit() else x)

# Resultado final
df_pivotadowawa.head()


PDV  SKU_FINAL                             DESCRICAO  C202411  C202412  \
0  12522       1004         FLORATTA DES COL MY BLUE 75ml      1.0      5.0   
1  12522       1080  INTENSE GLOS LAB BUBBAL TUT/FRUT 5ml      0.0      4.0   
2  12522       1296   PMPCK THE BLEND DES ANTIT AER 2x75g      0.0      6.0   
3  12522       1302        PMPCK LILY DES ANTIT AER 2x75g      0.0      8.0   
4  12522       1314        PMPCK ZAAD DES ANTIT AER 2x75g      0.0      4.0   

   C202413  C202414  C202501  C202502  C202503  C202504  C202505  C202506  \
0     56.0      6.0      1.0     11.0      1.0      5.0      9.0      5.0   
1     10.0      2.0      2.0      1.0      2.0      3.0      2.0      0.0   
2      2.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0   
3      6.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0   
4      1.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0   

   C202507  C202508  C202509  C202510  C202511  
0      8.0      1.0      7.0      3.0      0.0  
1     10.0     14.0      0.0      0.0      0.0  
2      0.0      0.0      0.0      0.0      2.0  
3      4.0      3.0      6.0      1.0      5.0  
4      0.0      0.0      1.0      1.0      1.0

In [11]:
df_pivotadowawa[ (df_pivotadowawa['PDV'] == '20998')].head()

PDV  SKU_FINAL                             DESCRICAO  C202411  \
75335  20998       1004         FLORATTA DES COL MY BLUE 75ml      5.0   
75336  20998       1005      DEM FLORATTA DES COL MY BLUE 4ml      0.0   
75337  20998       1062           NIINA SECRETS DES COL 100ml      0.0   
75338  20998       1073   NIINA SECRETS LOC DES HID CPO 200ml      0.0   
75339  20998       1080  INTENSE GLOS LAB BUBBAL TUT/FRUT 5ml      2.0   

       C202412  C202413  C202414  C202501  C202502  C202503  C202504  C202505  \
75335     37.0    479.0    131.0     16.0    252.0     96.0     39.0    170.0   
75336      0.0      0.0      1.0      0.0      0.0      0.0      2.0      2.0   
75337     53.0      5.0      9.0      3.0      4.0     19.0      3.0      5.0   
75338      2.0      1.0      8.0      5.0      1.0     13.0      0.0      1.0   
75339      7.0     58.0     14.0     19.0      2.0      7.0     23.0     45.0   

       C202506  C202507  C202508  C202509  C202510  C202511  
75335    142.0    101.0     17.0     31.0     20.0     10.0  
75336      0.0      1.0      0.0      2.0      3.0      1.0  
75337     14.0      5.0     38.0      0.0      3.0      9.0  
75338     11.0      3.0      6.0      0.0      1.0      0.0  
75339      1.0      2.0      4.0      0.0      0.0      0.0

In [12]:


df_pdv = pd.read_excel(r"C:\Users\joao.herculano\Documents\PDV_ATT.xlsx")

df_pdv_origi = pd.read_excel(r"C:\Users\joao.herculano\Documents\PDV_ATT.xlsx")

df_pdv = df_pdv.rename(columns={'DESCRIÇÃO':'DESCRIÇÃO PDV'})

df_pdv = df_pdv[df_pdv['GESTÃO']!="Inativa"]

df_pdv = df_pdv.drop(columns=['REGIÃO', 'ESTADO','CIDADE','GESTÃO', 'STATUS'])

df_pdv = df_pdv[df_pdv['CANAL']!='MTZ']

#df_pdv['CANAL'] = np.where((df_pdv['CANAL']=='LJ')|(df_pdv['CANAL']=='HIB')|(df_pdv['CANAL']=='CD'),'TODOS','VD')

df_pdv['MATCH'] = 1

df_pdv = df_pdv[(df_pdv['PDV']==910291)|(df_pdv['PDV']==910173)|(df_pdv['CANAL']=="VD")|(df_pdv['CANAL']=="HIB")|(df_pdv['CANAL']=="CD")]



In [13]:
df_pdv['PDV'].value_counts()

PDV
20968     1
20969     1
20970     1
20986     1
20988     1
20989     1
20991     1
20992     1
20993     1
20994     1
20995     1
20996     1
20997     1
20998     1
20999     1
21000     1
21001     1
21278     1
21375     1
21383     1
21495     1
22541     1
23703     1
23704     1
23708     1
23711     1
23712     1
24255     1
24257     1
24269     1
24293     1
910173    1
910291    1
23813     1
Name: count, dtype: int64

In [14]:
df_pdv = df_pdv.drop(columns=['PDV DESC'])

In [15]:
conn = pyodbc.connect(
    f"DRIVER={{SQL Server}};"
    f"SERVER={config['banco']['host']},1433;"
    f"DATABASE=GINSENG;"
    f"UID={config['banco']['user']};"
    f"PWD={config['banco']['password']}"
)

query_est_draft = f'''
select em.PDV ,
COALESCE(em.SKU_PARA , em.SKU) as SKU,
em.DESCRICAO,
d.salescurve as curva,
d.codcategory as categoria,
d.nextcycleprojection as proj_mar
,d.secondtonextcycleprojection as 'proj_mar+1',
em.[ESTOQUE ATUAL],em.[ESTOQUE EM TRANSITO],
em.[PEDIDO PENDENTE],
em.[DDV PREVISTO] ,
d.pricesellin as 'preço'
from estoque_mar em 
left join draft d on d.code = COALESCE(em.SKU_PARA , em.SKU) and d.loja_id = em.PDV 
where em.ORIGEM = 'QDB'
'''
df_draft_ = pd.read_sql(query_est_draft, conn)
conn.close()

#FALTA ATUALIZAR QUERY

C:\Users\joao.herculano\AppData\Local\Temp\ipykernel_43676\2995648402.py:25: UserWarning: pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.
  df_draft_ = pd.read_sql(query_est_draft, conn)


In [16]:
df_draft = df_draft_

In [17]:
df_draft.head()

PDV    SKU                                 DESCRICAO curva  categoria  \
0  20998  58191              QDB BAT EF MAT BERE 430 4,0g     E  MAQUIAGEM   
1  20998  87476  QDB BAT LIQ CR DOS SONHOS MARRONZ V2 4ml     B  MAQUIAGEM   
2  20998  87476   QDB BAT LIQ CREM DOS SONHOS MARRONZ 4ml     B  MAQUIAGEM   
3  20998  56945        QDB BAT LIQ INSTAMATTE AVELALI 4ml     B  MAQUIAGEM   
4  20998  56855        QDB BAT LIQ INSTAMATTE BORDOLI 4ml     B  MAQUIAGEM   

   proj_mar  proj_mar+1 ESTOQUE ATUAL ESTOQUE EM TRANSITO PEDIDO PENDENTE  \
0       5.0         0.0            36                   0               0   
1       1.0         0.0             3                   0               0   
2       1.0         0.0             3                   0               0   
3       1.0         0.0             1                   1               0   
4       0.0         0.0             1                   0               0   

  DDV PREVISTO  preço  
0         0,74   7.44  
1         0,07  11.92  
2         None  11.92  
3         0,05  11.92  
4            0  11.92

In [18]:
df_draft = df_draft[~df_draft['DESCRICAO'].str.contains('OUI', na=False)]

df_draft.shape

(39857, 12)

In [19]:
df_draft['ESTOQUE ATUAL'] = df_draft['ESTOQUE ATUAL'].astype(float)

df_draft['ESTOQUE EM TRANSITO'] = df_draft['ESTOQUE EM TRANSITO'].astype(float)

df_draft['PEDIDO PENDENTE'] = df_draft['PEDIDO PENDENTE'].astype(float)

df_draft.dtypes

PDV                     object
SKU                     object
DESCRICAO               object
curva                   object
categoria               object
proj_mar               float64
proj_mar+1             float64
ESTOQUE ATUAL          float64
ESTOQUE EM TRANSITO    float64
PEDIDO PENDENTE        float64
DDV PREVISTO            object
preço                  float64
dtype: object

In [20]:
df_draft['DDV PREVISTO'] = df_draft['DDV PREVISTO'].str.replace(',','.')

df_draft['DDV PREVISTO'] = df_draft['DDV PREVISTO'].astype(float)

df_draft['DDV PREVISTO'] = df_draft['DDV PREVISTO'].fillna(0)

In [21]:
df_draft.tail()

PDV    SKU                                 DESCRICAO curva  \
39852   20968  59167  CJ SCH QDB BAS TINT 290F/292O/300N 3x2ml  None   
39853   23704  42973             QDB BOLSA TRANSVERSAL PVC C/A  None   
39854  910291  53283       QDB BATOM VOLUMAO MARSALE 3,4G RPCK  None   
39855   23704  88602          QDB BAT HID COBRETE RPCK V2 3,8g  None   
39856   20969  70795          QDB LAPIS OLHOS BERINJELITO 1,2g  None   

      categoria  proj_mar  proj_mar+1  ESTOQUE ATUAL  ESTOQUE EM TRANSITO  \
39852      None       NaN         NaN            0.0                  0.0   
39853      None       NaN         NaN            0.0                  0.0   
39854      None       NaN         NaN            0.0                  0.0   
39855      None       NaN         NaN            0.0                  0.0   
39856      None       NaN         NaN            0.0                  0.0   

       PEDIDO PENDENTE  DDV PREVISTO  preço  
39852              0.0           0.0    NaN  
39853              0.0           0.0    NaN  
39854              0.0           0.0    NaN  
39855              0.0           0.0    NaN  
39856              0.0           0.0    NaN

In [22]:
#df_draft = df_draft.groupby(['PDV','SKU','curva','categoria'])[['proj_mar','proj_mar+1','ESTOQUE ATUAL','ESTOQUE EM TRANSITO','PEDIDO PENDENTE','DDV PREVISTO','preço']].max().reset_index() #TALVEZ TROLL

In [23]:
df_tabela = df_tabela.drop_duplicates()

In [24]:
df_bi_preco = pd.read_excel(r"C:\Users\joao.herculano\GRUPO GINSENG\Assistência Suprimentos - 2025\SUPRIMENTOS\DB_PROMOÇÕES\BOTICARIO\C13\preço BI\TABELA DE PREÇOS (2).xlsx")

df_bi_preco = df_bi_preco.drop(columns=['Tipo Preço','CATEGORIA','LINHA','MARCA'])



In [25]:

df_pivotadowawa['SKU_FINAL'] = df_pivotadowawa['SKU_FINAL'].astype(str)

df_pivotadowawa['SKU_FINAL'].head()

0    1004
1    1080
2    1296
3    1302
4    1314
Name: SKU_FINAL, dtype: object

In [26]:
df_pivotadowawa[df_pivotadowawa['PDV']=='910173']

Empty DataFrame
Columns: [PDV, SKU_FINAL, DESCRICAO, C202411, C202412, C202413, C202414, C202501, C202502, C202503, C202504, C202505, C202506, C202507, C202508, C202509, C202510, C202511]
Index: []

In [27]:
df_draft = pd.merge(df_draft,df_pivotadowawa,left_on=['PDV','SKU'],right_on=['PDV','SKU_FINAL'],how='left')

In [28]:
df_draft[df_draft['PDV']=='910173']

PDV    SKU                               DESCRICAO_x curva  \
11311  910173  74192      DESOBEDIENCIA CREME HID DES CPO 200g     B   
11403  910173  88722  QDB BALM LAB CREAM VERM TOD/FLORZINHA 5g     A   
11567  910173  56324     QDB BALM LAB HOGWARTS SORV/LIMAO 3,2g     B   
11595  910173  88738    QDB BALM LAB HOGW LESMAS/GEL/VERM 3,2g     E   
11618  910173  88739  QDB BALM LAB HOGW PENAS/ACUCAR/ROSA 3,2g     E   
...       ...    ...                                       ...   ...   
41161  910173  75242        QDB BAT LIQ SUPERMATE NUDELILI 4ml  None   
41178  910173  53000            QDB SHAMP SOLIDO RECARREGA 90g  None   
41251  910173  42115                         QDB PINCEL PO VS2  None   
41256  910173  50133  QDB BAT LIQ MATE FINERR ROSA TO/JOGO 5ml  None   
41376  910173  79775         QDB CORRET FAC AQUA HID COR 6 9ml  None   

                 categoria  proj_mar  proj_mar+1  ESTOQUE ATUAL  \
11311  CUIDADOS COM A PELE       6.0         3.0            1.0   
11403            MAQUIAGEM       7.0         6.0            0.0   
11567            MAQUIAGEM       5.0         3.0           11.0   
11595            MAQUIAGEM       6.0         3.0          170.0   
11618            MAQUIAGEM       6.0         3.0           97.0   
...                    ...       ...         ...            ...   
41161                 None       NaN         NaN            1.0   
41178                 None       NaN         NaN            6.0   
41251                 None       NaN         NaN            0.0   
41256                 None       NaN         NaN            2.0   
41376                 None       NaN         NaN            0.0   

       ESTOQUE EM TRANSITO  PEDIDO PENDENTE  ...  C202502  C202503 C202504  \
11311                  2.0              0.0  ...      NaN      NaN     NaN   
11403                  0.0              0.0  ...      NaN      NaN     NaN   
11567                  0.0              0.0  ...      NaN      NaN     NaN   
11595                  0.0              0.0  ...      NaN      NaN     NaN   
11618                  0.0              0.0  ...      NaN      NaN     NaN   
...                    ...              ...  ...      ...      ...     ...   
41161                  0.0              0.0  ...      NaN      NaN     NaN   
41178                  0.0              0.0  ...      NaN      NaN     NaN   
41251                  0.0              0.0  ...      NaN      NaN     NaN   
41256                  0.0              0.0  ...      NaN      NaN     NaN   
41376                  0.0              0.0  ...      NaN      NaN     NaN   

      C202505  C202506  C202507  C202508  C202509  C202510  C202511  
11311     NaN      NaN      NaN      NaN      NaN      NaN      NaN  
11403     NaN      NaN      NaN      NaN      NaN      NaN      NaN  
11567     NaN      NaN      NaN      NaN      NaN      NaN      NaN  
11595     NaN      NaN      NaN      NaN      NaN      NaN      NaN  
11618     NaN      NaN      NaN      NaN      NaN      NaN      NaN  
...       ...      ...      ...      ...      ...      ...      ...  
41161     NaN      NaN      NaN      NaN      NaN      NaN      NaN  
41178     NaN      NaN      NaN      NaN      NaN      NaN      NaN  
41251     NaN      NaN      NaN      NaN      NaN      NaN      NaN  
41256     NaN      NaN      NaN      NaN      NaN      NaN      NaN  
41376     NaN      NaN      NaN      NaN      NaN      NaN      NaN  

[906 rows x 29 columns]

In [29]:
df_draft[df_draft['SKU']=='1634']

Empty DataFrame
Columns: [PDV, SKU, DESCRICAO_x, curva, categoria, proj_mar, proj_mar+1, ESTOQUE ATUAL, ESTOQUE EM TRANSITO, PEDIDO PENDENTE, DDV PREVISTO, preço, SKU_FINAL, DESCRICAO_y, C202411, C202412, C202413, C202414, C202501, C202502, C202503, C202504, C202505, C202506, C202507, C202508, C202509, C202510, C202511]
Index: []

[0 rows x 29 columns]

In [30]:
df_final = pd.merge(left=df_tabela,right=df_pdv,on='MATCH',how='left')

df_final = df_final.drop_duplicates()

df_final.shape

(3672, 33)

In [31]:
df_pdv['PDV'].value_counts()

PDV
20968     1
20969     1
20970     1
20986     1
20988     1
20989     1
20991     1
20992     1
20993     1
20994     1
20995     1
20996     1
20997     1
20998     1
20999     1
21000     1
21001     1
21278     1
21375     1
21383     1
21495     1
22541     1
23703     1
23704     1
23708     1
23711     1
23712     1
24255     1
24257     1
24269     1
24293     1
910173    1
910291    1
23813     1
Name: count, dtype: int64

In [32]:
df_final['PDV'].value_counts()

PDV
20968     108
20969     108
20970     108
20986     108
20988     108
20989     108
20991     108
20992     108
20993     108
20994     108
20995     108
20996     108
20997     108
20998     108
20999     108
21000     108
21001     108
21278     108
21375     108
21383     108
21495     108
22541     108
23703     108
23704     108
23708     108
23711     108
23712     108
24255     108
24257     108
24269     108
24293     108
910173    108
910291    108
23813     108
Name: count, dtype: int64

In [33]:
df_draft.columns

Index(['PDV', 'SKU', 'DESCRICAO_x', 'curva', 'categoria', 'proj_mar',
       'proj_mar+1', 'ESTOQUE ATUAL', 'ESTOQUE EM TRANSITO', 'PEDIDO PENDENTE',
       'DDV PREVISTO', 'preço', 'SKU_FINAL', 'DESCRICAO_y', 'C202411',
       'C202412', 'C202413', 'C202414', 'C202501', 'C202502', 'C202503',
       'C202504', 'C202505', 'C202506', 'C202507', 'C202508', 'C202509',
       'C202510', 'C202511'],
      dtype='object')

In [34]:
df_draft = df_draft.drop(columns='DESCRICAO_y')

df_draft.columns

Index(['PDV', 'SKU', 'DESCRICAO_x', 'curva', 'categoria', 'proj_mar',
       'proj_mar+1', 'ESTOQUE ATUAL', 'ESTOQUE EM TRANSITO', 'PEDIDO PENDENTE',
       'DDV PREVISTO', 'preço', 'SKU_FINAL', 'C202411', 'C202412', 'C202413',
       'C202414', 'C202501', 'C202502', 'C202503', 'C202504', 'C202505',
       'C202506', 'C202507', 'C202508', 'C202509', 'C202510', 'C202511'],
      dtype='object')

In [35]:
df_draft.columns[-15:]

Index(['C202411', 'C202412', 'C202413', 'C202414', 'C202501', 'C202502',
       'C202503', 'C202504', 'C202505', 'C202506', 'C202507', 'C202508',
       'C202509', 'C202510', 'C202511'],
      dtype='object')

In [36]:
numericos = df_draft.columns[-15:]

chaves = [col for col in df_draft.columns if col not in numericos]

# 2. Fazer o groupby
df_draft_agg = (
    df_draft
    .groupby(chaves, as_index=False)[numericos]
    .max()
)

df_draft_agg['PDV'].value_counts()

PDV
20998    448
20997    423
23711    420
20993    390
20996    374
21278    363
20994    315
22541    308
20995    306
20970    287
20989    278
24255    277
20992    275
21375    254
23704    251
20999    250
21495    245
20969    245
21383    245
21000    239
20991    235
21001    230
20988    211
20968    205
23703    191
20986    183
23712    148
24257    146
24269    116
24293     96
23813     52
23708     14
Name: count, dtype: int64

In [37]:
df_draft_[df_draft_['PDV']=='910173']

PDV    SKU                                 DESCRICAO curva  \
10305  910173  74192      DESOBEDIENCIA CREME HID DES CPO 200g     B   
10391  910173  88722  QDB BALM LAB CREAM VERM TOD/FLORZINHA 5g     A   
10536  910173  56324     QDB BALM LAB HOGWARTS SORV/LIMAO 3,2g     B   
10560  910173  88738    QDB BALM LAB HOGW LESMAS/GEL/VERM 3,2g     E   
10583  910173  88739  QDB BALM LAB HOGW PENAS/ACUCAR/ROSA 3,2g     E   
...       ...    ...                                       ...   ...   
39580  910173  75242        QDB BAT LIQ SUPERMATE NUDELILI 4ml  None   
39597  910173  53000            QDB SHAMP SOLIDO RECARREGA 90g  None   
39670  910173  42115                         QDB PINCEL PO VS2  None   
39675  910173  50133  QDB BAT LIQ MATE FINERR ROSA TO/JOGO 5ml  None   
39793  910173  79775         QDB CORRET FAC AQUA HID COR 6 9ml  None   

                 categoria  proj_mar  proj_mar+1 ESTOQUE ATUAL  \
10305  CUIDADOS COM A PELE       6.0         3.0             1   
10391            MAQUIAGEM       7.0         6.0             0   
10536            MAQUIAGEM       5.0         3.0            11   
10560            MAQUIAGEM       6.0         3.0           170   
10583            MAQUIAGEM       6.0         3.0            97   
...                    ...       ...         ...           ...   
39580                 None       NaN         NaN             1   
39597                 None       NaN         NaN             6   
39670                 None       NaN         NaN             0   
39675                 None       NaN         NaN             2   
39793                 None       NaN         NaN             0   

      ESTOQUE EM TRANSITO PEDIDO PENDENTE DDV PREVISTO  preço  
10305                   2               0         0,14  13.47  
10391                   0               0         0,18  16.06  
10536                   0               0         0,19  14.48  
10560                   0               0         0,23  13.16  
10583                   0               0         0,23  13.16  
...                   ...             ...          ...    ...  
39580                   0               0         None    NaN  
39597                   0               0         None    NaN  
39670                   0               0         None    NaN  
39675                   0               0         None    NaN  
39793                   0               0         None    NaN  

[906 rows x 12 columns]

In [38]:
df_draft[df_draft['SKU']=='1634']

Empty DataFrame
Columns: [PDV, SKU, DESCRICAO_x, curva, categoria, proj_mar, proj_mar+1, ESTOQUE ATUAL, ESTOQUE EM TRANSITO, PEDIDO PENDENTE, DDV PREVISTO, preço, SKU_FINAL, C202411, C202412, C202413, C202414, C202501, C202502, C202503, C202504, C202505, C202506, C202507, C202508, C202509, C202510, C202511]
Index: []

[0 rows x 28 columns]

In [39]:
df_draft1 = df_draft_agg

In [40]:
df_draft1.columns

Index(['PDV', 'SKU', 'DESCRICAO_x', 'curva', 'categoria', 'proj_mar',
       'proj_mar+1', 'ESTOQUE ATUAL', 'ESTOQUE EM TRANSITO', 'PEDIDO PENDENTE',
       'DDV PREVISTO', 'preço', 'SKU_FINAL', 'C202411', 'C202412', 'C202413',
       'C202414', 'C202501', 'C202502', 'C202503', 'C202504', 'C202505',
       'C202506', 'C202507', 'C202508', 'C202509', 'C202510', 'C202511'],
      dtype='object')

In [41]:
df_draft1.to_clipboard()

In [42]:
df_final['PDV'] = df_final['PDV'].astype('str')
df_final['Código'] = df_final['Código'].astype('str')


df_final = pd.merge(left=df_final,right=df_draft1,left_on=['PDV','Código'],right_on=['PDV','SKU'],how='left')
df_final.shape

(3771, 60)

In [43]:
df_final[df_final['Código']=='1634'].head()

Empty DataFrame
Columns: [Ciclo, Região, Canal, Código, Descrição, IAF, Tipo de pedido, Foco, Unidade de negócio, Marca, Categoria, Subcategoria, Quantidade por caixa, Tipo de promoção, Catálogo, Tipo de produto, Ação consumidor, Percentual de desconto consumidor, Ação revendedor, Percentual de desconto revendedor, Sortimento P, Sortimento M, Sortimento G, MATCH, PDV, CANAL, DESCRIÇÃO PDV, UF, MARCA, ANALISTA, SUPERVISOR, SUP, ANALISTA EUD, SKU, DESCRICAO_x, curva, categoria, proj_mar, proj_mar+1, ESTOQUE ATUAL, ESTOQUE EM TRANSITO, PEDIDO PENDENTE, DDV PREVISTO, preço, SKU_FINAL, C202411, C202412, C202413, C202414, C202501, C202502, C202503, C202504, C202505, C202506, C202507, C202508, C202509, C202510, C202511]
Index: []

[0 rows x 60 columns]

In [44]:
df_final['PDV'].value_counts()

PDV
20997     117
20970     116
23711     116
20998     115
20993     115
20996     114
21278     113
20969     112
20995     112
20992     112
21383     112
21000     112
21001     112
20994     112
22541     112
20989     111
20999     110
20991     110
21495     110
20986     110
20988     110
21375     110
20968     109
23712     109
23704     108
23703     108
23708     108
24255     108
24257     108
24269     108
24293     108
910173    108
910291    108
23813     108
Name: count, dtype: int64

In [45]:
df_final = df_final.drop(columns=['Sortimento P', 'Sortimento M',
       'Sortimento G','MARCA'])

In [46]:
calendario = pd.read_excel(r"C:\Users\joao.herculano\GRUPO GINSENG\Assistência Suprimentos - 2025\SUPRIMENTOS\BD_LANÇAMENTOS\BASE DE DADOS LANÇAMENTO\BOT\CICLO 9\CALENDARIO_CICLO\Ciclo_Expandido_com_Datas.xlsx")


In [47]:
calendario['Date'] = pd.to_datetime(calendario['Date'])

# Get today (normalized to midnight)
today = pd.Timestamp("today").normalize()

calendario['NUM_CICLO'] = calendario['Ciclo'].str[-2:].astype(int)
calendario['ANO_CICLO'] = calendario['Ciclo'].str[0:5]


calendario = calendario[calendario['MARCA'] == "BOTICARIO"]

calendario = calendario.drop(columns='MARCA')

calendario['CICLOMAIS2'] = calendario['ANO_CICLO'].astype(str) + (calendario['NUM_CICLO'].astype(int) + 2).astype(str).str.zfill(2) # >>>>>>>>> MUDAR PRA CICLO CORRETO 

ciclo_mais2 = calendario[calendario['Date'].dt.normalize() == today]['CICLOMAIS2'].iloc[0]


# Filter rows where date matches today
filtered_calendario = calendario[calendario['Ciclo'] == ciclo_mais2][:1]


filtered_calendario['dias_ate_inicio'] = filtered_calendario['INICIO CICLO'].iloc[0] - today

filtered_calendario['dias_ate_inicio'] = filtered_calendario['dias_ate_inicio'].dt.days.astype(int)

filtered_calendario


Ciclo INICIO CICLO  FIM CICLO  DURAÇÃO       Date  NUM_CICLO  \
2409  C202515   2025-10-13 2025-11-02       21 2025-10-13         15   

     ANO_CICLO CICLOMAIS2  dias_ate_inicio  
2409     C2025    C202517               24

In [48]:
filtered_calendario['MATCH'] = 1

In [49]:
df_pdv['UF'] = np.where(df_pdv['UF'] == 'VDC','BA',df_pdv['UF'])

In [50]:
df_draft['PDV'] = df_draft['PDV'].astype(str)

In [51]:
df_draft['PDV'].value_counts()

PDV
20997    2749
20992    2646
20969    2639
21007    1592
20998    1430
         ... 
20006      57
24258       2
24254       2
24253       2
24268       2
Name: count, Length: 80, dtype: int64

In [52]:
df_final = pd.merge(left=df_final, right=filtered_calendario[['Ciclo','INICIO CICLO','FIM CICLO','DURAÇÃO','MATCH','dias_ate_inicio']], on='MATCH',how='left')
df_final.shape

(3771, 61)

In [53]:
df_final['Código'] = df_final['Código'].astype('Int64') 
df_final['PDV'] = df_final['PDV'].astype('Int64') 

In [54]:
df_bi_preco['SKU2'] = df_bi_preco['SKU2'].astype('Int64')
df_bi_preco.head()

SKU1   SKU2                            Descrição  UF      PC      PV  \
0  84918  84918  ESTJ BOTI CALENDARIO ADVENTO NAT/24  AL  393.70  1300.0   
1  84918  84918  ESTJ BOTI CALENDARIO ADVENTO NAT/24  BA  436.73  1300.0   
2  84918  84918  ESTJ BOTI CALENDARIO ADVENTO NAT/24  SE  379.94  1300.0   
3  54230  54230         MALBEC DES COL 20 ANOS 100ml  AL  138.54   499.9   
4  54230  54230         MALBEC DES COL 20 ANOS 100ml  BA  148.66   499.9   

  chave sku2 chave sku1  
0    AL84918    AL84918  
1    BA84918    BA84918  
2    SE84918    SE84918  
3    AL54230    AL54230  
4    BA54230    BA54230

In [55]:


df_final = pd.merge(left=df_final,right=df_bi_preco,right_on=['UF','SKU2'],left_on=['UF','Código'],how='left')
df_final.shape   

(3771, 68)

In [56]:
df_bi_preco['SKU1'] = df_bi_preco['SKU1'].fillna(0)

In [57]:
# Conversão segura para Int64 (nullable)
df_bi_preco['SKU1'] = pd.to_numeric(df_bi_preco['SKU1'], errors='coerce').astype('Int64')

# Realiza o merge
df_final = pd.merge(
    left=df_final,
    right=df_bi_preco[['SKU1', 'SKU2', 'UF', 'PC', 'PV']],
    right_on=['UF', 'SKU1'],
    left_on=['UF', 'Código'],
    how='left'
)

# Verifica o resultado
print(df_final.shape)


(3771, 72)


In [58]:
df_final['PRECO DE COMPRA'] = np.where(~df_final['PC_x'].isna(),df_final['PC_x'],df_final['PC_y'])

df_final['PRECO DE VENDA'] = np.where(~df_final['PV_x'].isna(),df_final['PV_x'],df_final['PV_y'])



In [59]:
df_final['CANAL'] = np.where((df_final['CANAL'] == 'LJ') | (df_final['CANAL'] == 'HIB'), "TODOS" , np.where((df_final['CANAL'] == 'CD') | (df_final['CANAL'] == 'VD'), "VD", df_final['CANAL']))

df_final['CANAL'].value_counts()

CANAL
TODOS    1973
VD       1798
Name: count, dtype: int64

In [60]:
df_final = df_final.drop_duplicates()

In [61]:
df_final = df_final.drop(columns=['SKU1_x','SKU1_y','SKU2_x','SKU2_y','PC_x', 'PV_x','PC_y', 'PV_y','Subcategoria',
'Quantidade por caixa'
])

In [62]:
df_final['UFPRODUTO'] = df_final['UF'].astype(str) + df_final['Código'].astype(str)


In [63]:
df_final = df_final.rename(columns={'Compra inteligente Próximo Ciclo + 1':'Compra inteligente Próximo Ciclo','Arquivo_Origem': 'MARCA'})

In [64]:
df_final = df_final[~df_final['Marca'].isna()]
df_final['Marca'].isna().sum()

np.int64(0)

In [65]:
df_final.columns

Index(['Ciclo_x', 'Região', 'Canal', 'Código', 'Descrição_x', 'IAF',
       'Tipo de pedido', 'Foco', 'Unidade de negócio', 'Marca', 'Categoria',
       'Tipo de promoção', 'Catálogo', 'Tipo de produto', 'Ação consumidor',
       'Percentual de desconto consumidor', 'Ação revendedor',
       'Percentual de desconto revendedor', 'MATCH', 'PDV', 'CANAL',
       'DESCRIÇÃO PDV', 'UF', 'ANALISTA', 'SUPERVISOR', 'SUP', 'ANALISTA EUD',
       'SKU', 'DESCRICAO_x', 'curva', 'categoria', 'proj_mar', 'proj_mar+1',
       'ESTOQUE ATUAL', 'ESTOQUE EM TRANSITO', 'PEDIDO PENDENTE',
       'DDV PREVISTO', 'preço', 'SKU_FINAL', 'C202411', 'C202412', 'C202413',
       'C202414', 'C202501', 'C202502', 'C202503', 'C202504', 'C202505',
       'C202506', 'C202507', 'C202508', 'C202509', 'C202510', 'C202511',
       'Ciclo_y', 'INICIO CICLO', 'FIM CICLO', 'DURAÇÃO', 'dias_ate_inicio',
       'Descrição_y', 'chave sku2', 'chave sku1', 'PRECO DE COMPRA',
       'PRECO DE VENDA', 'UFPRODUTO'],
      dtype='o

In [66]:
df_vdc = pd.read_csv(r"C:\Users\joao.herculano\GRUPO GINSENG\Assistência Suprimentos - 2025\SUPRIMENTOS\DB_PROMOÇÕES\BOTICARIO\C10\VENDA VITORIA 2024\VENDA VITORIA.csv")

df_vdc['PRODUTO'] = df_vdc['PRODUTO'].astype('Int64')

df_final['Código'] = df_final['Código'].astype('Int64')

df_final =pd.merge(left=df_final,right=df_vdc,left_on= ['PDV','Código'],right_on= ['PDV GINSENG','PRODUTO'],how='left' )

df_final[df_final.columns[-1]] = df_final[df_final.columns[-1]].fillna(0)

In [67]:
df_vdc[df_vdc['PRODUTO']== 74043].head()

PDV GINSENG  PRODUTO  202401  202402  202403  202404  202405  202406  \
1235        23701    74043      12      24      12      16       8      14   
3033        23702    74043       2      22       8      22      10      14   
5171        23703    74043      10      18       6      18       6       2   

      202407  202408  202409  202410  202411  202412  202413  202414  202415  \
1235       6      14      12       0       8      10       4      42       0   
3033      14      10      12       8      22       6      14      36      10   
5171      20       0      10       2      22       4       2      26       2   

      202416  
1235      14  
3033       0  
5171      16

In [68]:
df_final = df_final.fillna(0)


In [69]:
df_final.columns

Index(['Ciclo_x', 'Região', 'Canal', 'Código', 'Descrição_x', 'IAF',
       'Tipo de pedido', 'Foco', 'Unidade de negócio', 'Marca', 'Categoria',
       'Tipo de promoção', 'Catálogo', 'Tipo de produto', 'Ação consumidor',
       'Percentual de desconto consumidor', 'Ação revendedor',
       'Percentual de desconto revendedor', 'MATCH', 'PDV', 'CANAL',
       'DESCRIÇÃO PDV', 'UF', 'ANALISTA', 'SUPERVISOR', 'SUP', 'ANALISTA EUD',
       'SKU', 'DESCRICAO_x', 'curva', 'categoria', 'proj_mar', 'proj_mar+1',
       'ESTOQUE ATUAL', 'ESTOQUE EM TRANSITO', 'PEDIDO PENDENTE',
       'DDV PREVISTO', 'preço', 'SKU_FINAL', 'C202411', 'C202412', 'C202413',
       'C202414', 'C202501', 'C202502', 'C202503', 'C202504', 'C202505',
       'C202506', 'C202507', 'C202508', 'C202509', 'C202510', 'C202511',
       'Ciclo_y', 'INICIO CICLO', 'FIM CICLO', 'DURAÇÃO', 'dias_ate_inicio',
       'Descrição_y', 'chave sku2', 'chave sku1', 'PRECO DE COMPRA',
       'PRECO DE VENDA', 'UFPRODUTO', 'PDV GINSENG', 

In [70]:
df_final.columns[-16:]

Index(['202401', '202402', '202403', '202404', '202405', '202406', '202407',
       '202408', '202409', '202410', '202411', '202412', '202413', '202414',
       '202415', '202416'],
      dtype='object')

In [71]:
df_final.to_clipboard()

In [72]:
import re

# identificar colunas de ciclo puro (ex: '202407')
colunas_ciclo_puro = [col for col in df_final.columns[-16:]]

for col in colunas_ciclo_puro:
    col_hist = f'C{col}'
    if col_hist in df_final.columns:
        # mantém o maior valor entre a coluna histórica e a pura
        df_final[col_hist] = df_final[[col_hist, col]].max(axis=1)

# remove as colunas puras
if colunas_ciclo_puro:
    df_final.drop(columns=colunas_ciclo_puro, inplace=True)


In [73]:
df_final.columns

Index(['Ciclo_x', 'Região', 'Canal', 'Código', 'Descrição_x', 'IAF',
       'Tipo de pedido', 'Foco', 'Unidade de negócio', 'Marca', 'Categoria',
       'Tipo de promoção', 'Catálogo', 'Tipo de produto', 'Ação consumidor',
       'Percentual de desconto consumidor', 'Ação revendedor',
       'Percentual de desconto revendedor', 'MATCH', 'PDV', 'CANAL',
       'DESCRIÇÃO PDV', 'UF', 'ANALISTA', 'SUPERVISOR', 'SUP', 'ANALISTA EUD',
       'SKU', 'DESCRICAO_x', 'curva', 'categoria', 'proj_mar', 'proj_mar+1',
       'ESTOQUE ATUAL', 'ESTOQUE EM TRANSITO', 'PEDIDO PENDENTE',
       'DDV PREVISTO', 'preço', 'SKU_FINAL', 'C202411', 'C202412', 'C202413',
       'C202414', 'C202501', 'C202502', 'C202503', 'C202504', 'C202505',
       'C202506', 'C202507', 'C202508', 'C202509', 'C202510', 'C202511',
       'Ciclo_y', 'INICIO CICLO', 'FIM CICLO', 'DURAÇÃO', 'dias_ate_inicio',
       'Descrição_y', 'chave sku2', 'chave sku1', 'PRECO DE COMPRA',
       'PRECO DE VENDA', 'UFPRODUTO', 'PDV GINSENG', 

In [74]:
df_irece = pd.read_csv(r"C:\Users\joao.herculano\GRUPO GINSENG\Assistência Suprimentos - 2025\DADOS DOURADO\VENDA\COMPILADO_VENDAS.csv", sep=';')

df_irece['DATA_VENDA'] = pd.to_datetime(df_irece['DATA_VENDA'], dayfirst=True)

df_irece = pd.merge(df_irece,calendario[['Ciclo','Date']],how='left', left_on='DATA_VENDA',right_on='Date')

df_irece.head()

DATA_VENDA    PDV  pdvs cp                                       DESC PDV  \
0 2025-04-01  12993    24253   PERFUMARIA E COSMETICOS QUEIROZ DOURADO LTDA   
1 2025-04-01  12993    24253   PERFUMARIA E COSMETICOS QUEIROZ DOURADO LTDA   
2 2025-04-01  12993    24253   PERFUMARIA E COSMETICOS QUEIROZ DOURADO LTDA   
3 2025-04-01  12993    24253   PERFUMARIA E COSMETICOS QUEIROZ DOURADO LTDA   
4 2025-04-01  12993    24253   PERFUMARIA E COSMETICOS QUEIROZ DOURADO LTDA   

   Código                                 Descrição  Quantidade Faturamento  \
0    1004             FLORATTA DES COL MY BLUE 75ml           1       98,99   
1    4539      BOTIK CR FAC FIRMADOR AC/HIAL 40g V2           1      129,05   
2   29046  BOTICOLL CONNEX DES BDY SPR 100ml V6 PCK           1        38,9   
3   47154                 CBEM DES ROLL S/ALUM 55ml           1       21,98   
4   47411                          ARBO NECESS LONA           1       57,26   

     Ciclo       Date  
0  C202505 2025-04-01  
1  C202505 2025-04-01  
2  C202505 2025-04-01  
3  C202505 2025-04-01  
4  C202505 2025-04-01

In [75]:
df_irece_agrupado = df_irece.groupby(['PDV','Código','Ciclo'])['Quantidade'].sum().reset_index()

df_pivotado = df_irece_agrupado.pivot(index=['PDV', 'Código'], columns='Ciclo', values='Quantidade').reset_index()

df_pivotado = df_pivotado.fillna(0)

In [76]:
df_final.columns[37:55]

Index(['preço', 'SKU_FINAL', 'C202411', 'C202412', 'C202413', 'C202414',
       'C202501', 'C202502', 'C202503', 'C202504', 'C202505', 'C202506',
       'C202507', 'C202508', 'C202509', 'C202510', 'C202511', 'Ciclo_y'],
      dtype='object')

In [77]:
for col_c in df_final.columns[37:55]:
    sufixo = col_c[1:]  # Remove o 'C' do início, ex: 'C202407' -> '202407'
    df_final.columns = df_final.columns.str.replace("C20", "20", regex=True)


df_final.columns

Index(['Ciclo_x', 'Região', 'Canal', 'Código', 'Descrição_x', 'IAF',
       'Tipo de pedido', 'Foco', 'Unidade de negócio', 'Marca', 'Categoria',
       'Tipo de promoção', 'Catálogo', 'Tipo de produto', 'Ação consumidor',
       'Percentual de desconto consumidor', 'Ação revendedor',
       'Percentual de desconto revendedor', 'MATCH', 'PDV', 'CANAL',
       'DESCRIÇÃO PDV', 'UF', 'ANALISTA', 'SUPERVISOR', 'SUP', 'ANALISTA EUD',
       'SKU', 'DESCRICAO_x', 'curva', 'categoria', 'proj_mar', 'proj_mar+1',
       'ESTOQUE ATUAL', 'ESTOQUE EM TRANSITO', 'PEDIDO PENDENTE',
       'DDV PREVISTO', 'preço', 'SKU_FINAL', '202411', '202412', '202413',
       '202414', '202501', '202502', '202503', '202504', '202505', '202506',
       '202507', '202508', '202509', '202510', '202511', 'Ciclo_y',
       'INICIO CICLO', 'FIM CICLO', 'DURAÇÃO', 'dias_ate_inicio',
       'Descrição_y', 'chave sku2', 'chave sku1', 'PRECO DE COMPRA',
       'PRECO DE VENDA', 'UFPRODUTO', 'PDV GINSENG', 'PRODUTO'],
   

In [78]:
df_final['PDV'].value_counts()

PDV
20997     117
20970     116
23711     116
20998     115
20993     115
20996     114
21278     113
20969     112
20995     112
20992     112
21383     112
21000     112
21001     112
20994     112
22541     112
20989     111
20999     110
20991     110
21495     110
20986     110
20988     110
21375     110
20968     109
23712     109
23704     108
23703     108
23708     108
24255     108
24257     108
24269     108
24293     108
910173    108
910291    108
23813     108
Name: count, dtype: Int64

In [79]:
df_final = pd.merge(df_final,df_pivotado,how='left',on=['PDV','Código'])

df_final = df_final.fillna(0)

df_final.head()

Ciclo_x Região  Canal  Código                      Descrição_x  IAF  \
0   202513    NNE  Todos   47196  QDB MASC CILIO BIG BANG 360 10g  Não   
1   202513    NNE  Todos   47196  QDB MASC CILIO BIG BANG 360 10g  Não   
2   202513    NNE  Todos   47196  QDB MASC CILIO BIG BANG 360 10g  Não   
3   202513    NNE  Todos   47196  QDB MASC CILIO BIG BANG 360 10g  Não   
4   202513    NNE  Todos   47196  QDB MASC CILIO BIG BANG 360 10g  Não   

  Tipo de pedido Foco Unidade de negócio                Marca  ... C202415  \
0       Especial  Sim                QDB  QUEM DISSE BERENICE  ...     0.0   
1       Especial  Sim                QDB  QUEM DISSE BERENICE  ...     0.0   
2       Especial  Sim                QDB  QUEM DISSE BERENICE  ...     0.0   
3       Especial  Sim                QDB  QUEM DISSE BERENICE  ...     0.0   
4       Especial  Sim                QDB  QUEM DISSE BERENICE  ...     0.0   

  C202416 C202417 C202501 C202502 C202503 C202504 C202505  C202506  C202507  
0     0.0     0.0     0.0     0.0     0.0     0.0     0.0      0.0      0.0  
1     0.0     0.0     0.0     0.0     0.0     0.0     0.0      0.0      0.0  
2     0.0     0.0     0.0     0.0     0.0     0.0     0.0      0.0      0.0  
3     0.0     0.0     0.0     0.0     0.0     0.0     0.0      0.0      0.0  
4     0.0     0.0     0.0     0.0     0.0     0.0     0.0      0.0      0.0  

[5 rows x 91 columns]

In [80]:
df_final.columns

Index(['Ciclo_x', 'Região', 'Canal', 'Código', 'Descrição_x', 'IAF',
       'Tipo de pedido', 'Foco', 'Unidade de negócio', 'Marca', 'Categoria',
       'Tipo de promoção', 'Catálogo', 'Tipo de produto', 'Ação consumidor',
       'Percentual de desconto consumidor', 'Ação revendedor',
       'Percentual de desconto revendedor', 'MATCH', 'PDV', 'CANAL',
       'DESCRIÇÃO PDV', 'UF', 'ANALISTA', 'SUPERVISOR', 'SUP', 'ANALISTA EUD',
       'SKU', 'DESCRICAO_x', 'curva', 'categoria', 'proj_mar', 'proj_mar+1',
       'ESTOQUE ATUAL', 'ESTOQUE EM TRANSITO', 'PEDIDO PENDENTE',
       'DDV PREVISTO', 'preço', 'SKU_FINAL', '202411', '202412', '202413',
       '202414', '202501', '202502', '202503', '202504', '202505', '202506',
       '202507', '202508', '202509', '202510', '202511', 'Ciclo_y',
       'INICIO CICLO', 'FIM CICLO', 'DURAÇÃO', 'dias_ate_inicio',
       'Descrição_y', 'chave sku2', 'chave sku1', 'PRECO DE COMPRA',
       'PRECO DE VENDA', 'UFPRODUTO', 'PDV GINSENG', 'PRODUTO', 'C20

In [81]:


# 1. Identificar colunas no formato 'C2024xx', 'C2025xx', etc.
colunas_ciclo_c = [col for col in df_pivotado.columns if re.fullmatch(r'C20\d{4}', col)]

for col_c in colunas_ciclo_c:
    sufixo = col_c[1:]  # Remove o 'C' do início, ex: 'C202407' -> '202407'
    col_hist = col_c
    
    if col_hist in df_final.columns:
        # Pega o maior valor entre a coluna de histórico e a de ciclo com "C"
        df_final[col_hist] = df_final[[col_hist, col_c]].max(axis=1)

# (Opcional) Remover as colunas 'C20xxxx' após o merge
df_final.drop(columns=colunas_ciclo_c, inplace=True)


In [82]:
df_final.columns

Index(['Ciclo_x', 'Região', 'Canal', 'Código', 'Descrição_x', 'IAF',
       'Tipo de pedido', 'Foco', 'Unidade de negócio', 'Marca', 'Categoria',
       'Tipo de promoção', 'Catálogo', 'Tipo de produto', 'Ação consumidor',
       'Percentual de desconto consumidor', 'Ação revendedor',
       'Percentual de desconto revendedor', 'MATCH', 'PDV', 'CANAL',
       'DESCRIÇÃO PDV', 'UF', 'ANALISTA', 'SUPERVISOR', 'SUP', 'ANALISTA EUD',
       'SKU', 'DESCRICAO_x', 'curva', 'categoria', 'proj_mar', 'proj_mar+1',
       'ESTOQUE ATUAL', 'ESTOQUE EM TRANSITO', 'PEDIDO PENDENTE',
       'DDV PREVISTO', 'preço', 'SKU_FINAL', '202411', '202412', '202413',
       '202414', '202501', '202502', '202503', '202504', '202505', '202506',
       '202507', '202508', '202509', '202510', '202511', 'Ciclo_y',
       'INICIO CICLO', 'FIM CICLO', 'DURAÇÃO', 'dias_ate_inicio',
       'Descrição_y', 'chave sku2', 'chave sku1', 'PRECO DE COMPRA',
       'PRECO DE VENDA', 'UFPRODUTO', 'PDV GINSENG', 'PRODUTO'],
   

In [83]:
colunas_ciclo_c = [col for col in df_pivotado.columns if re.fullmatch(r'C20\d{4}', col)]

for col_c in colunas_ciclo_c:
    sufixo = col_c[1:]  # Remove o 'C' do início, ex: 'C202407' -> '202407'
    col_hist = col_c
    print(sufixo,col_c)


202401 C202401
202402 C202402
202403 C202403
202404 C202404
202405 C202405
202406 C202406
202407 C202407
202408 C202408
202409 C202409
202410 C202410
202411 C202411
202412 C202412
202413 C202413
202414 C202414
202415 C202415
202416 C202416
202417 C202417
202501 C202501
202502 C202502
202503 C202503
202504 C202504
202505 C202505
202506 C202506
202507 C202507


In [84]:
df_final = df_final.drop(columns=['Ciclo_y'])

In [85]:
df_final.columns

Index(['Ciclo_x', 'Região', 'Canal', 'Código', 'Descrição_x', 'IAF',
       'Tipo de pedido', 'Foco', 'Unidade de negócio', 'Marca', 'Categoria',
       'Tipo de promoção', 'Catálogo', 'Tipo de produto', 'Ação consumidor',
       'Percentual de desconto consumidor', 'Ação revendedor',
       'Percentual de desconto revendedor', 'MATCH', 'PDV', 'CANAL',
       'DESCRIÇÃO PDV', 'UF', 'ANALISTA', 'SUPERVISOR', 'SUP', 'ANALISTA EUD',
       'SKU', 'DESCRICAO_x', 'curva', 'categoria', 'proj_mar', 'proj_mar+1',
       'ESTOQUE ATUAL', 'ESTOQUE EM TRANSITO', 'PEDIDO PENDENTE',
       'DDV PREVISTO', 'preço', 'SKU_FINAL', '202411', '202412', '202413',
       '202414', '202501', '202502', '202503', '202504', '202505', '202506',
       '202507', '202508', '202509', '202510', '202511', 'INICIO CICLO',
       'FIM CICLO', 'DURAÇÃO', 'dias_ate_inicio', 'Descrição_y', 'chave sku2',
       'chave sku1', 'PRECO DE COMPRA', 'PRECO DE VENDA', 'UFPRODUTO',
       'PDV GINSENG', 'PRODUTO'],
      dtype='o

In [86]:
df_final = df_final.drop_duplicates()
df_final.shape

(3771, 66)

In [87]:
df_final['chave'] = df_final['PDV'].astype('str') + df_final['Código'].astype('str')

In [88]:
df_final = df_final.fillna(0)


In [89]:
df_final.columns[39:54]

Index(['202411', '202412', '202413', '202414', '202501', '202502', '202503',
       '202504', '202505', '202506', '202507', '202508', '202509', '202510',
       '202511'],
      dtype='object')

In [90]:
# Define list of target columns
sales_2024_cols = df_final.columns[39:54]
# Create a new column with the row-wise max
df_final['PICO DE VENDAS 2024'] = df_final[sales_2024_cols].max(axis=1)



In [91]:
df_final.columns[47:54]

Index(['202505', '202506', '202507', '202508', '202509', '202510', '202511'], dtype='object')

In [92]:
vendas_6_meses = df_final.columns[47:54]

df_final['Pico Vendas Ultimos 6 ciclos'] = df_final[vendas_6_meses].max(axis=1)

In [93]:
df_final.columns[39:54]

Index(['202411', '202412', '202413', '202414', '202501', '202502', '202503',
       '202504', '202505', '202506', '202507', '202508', '202509', '202510',
       '202511'],
      dtype='object')

In [94]:
# Define as colunas mensais
colunas_mensais = df_final.columns[39:54]

# Função de cálculo por grupo
def calcular_crescimento(grupo):
    soma_mensal = grupo[colunas_mensais].sum()
    variacao_mensal = soma_mensal.pct_change().dropna()
    variacao_mensal = variacao_mensal[np.isfinite(variacao_mensal)]

    if len(variacao_mensal) == 0:
        return pd.Series({'CRESCIMENTO': np.nan})

    media = variacao_mensal.mean()
    desvio = variacao_mensal.std()

    limite_sup = media + 2 * desvio
    limite_inf = media - 2 * desvio

    variacoes_filtradas = variacao_mensal[variacao_mensal.between(limite_inf, limite_sup)]
    crescimento = round(variacoes_filtradas.mean(), 4)
    return pd.Series({'CRESCIMENTO': crescimento})

# Aplica a função por PDV
crescimento_por_pdv = (
    df_final
    .groupby('PDV')
    .apply(calcular_crescimento)   # retorna índice com PDV
    .reset_index(level=0)          # reseta só o nível PDV
)

# Merge do resultado de volta no dataframe original
df_final = df_final.merge(crescimento_por_pdv, on='PDV', how='left')


C:\Users\joao.herculano\AppData\Local\Temp\ipykernel_43676\3012255654.py:27: DeprecationWarning: DataFrameGroupBy.apply operated on the grouping columns. This behavior is deprecated, and in a future version of pandas the grouping columns will be excluded from the operation. Either pass `include_groups=False` to exclude the groupings or explicitly select the grouping columns after groupby to silence this warning.
  .apply(calcular_crescimento)   # retorna índice com PDV


In [95]:
# Suponha que os meses estão nas colunas 10 a 26 (17 colunas = 17 meses)
colunas_mensais = df_final.columns[39:54]

# Passo 1: Soma todas as linhas (itens) por mês → resultado: total por mês
soma_mensal = df_final[colunas_mensais].sum()

# Passo 2: Calcula a variação percentual de um mês para o outro
variacao_mensal = soma_mensal.pct_change()
variacao_mensal = variacao_mensal.dropna()

variacao_mensal = variacao_mensal[np.isfinite(variacao_mensal)]

# Passo 3: Calcula a média da variação (ignorando o primeiro NaN)
media_variacao = variacao_mensal[1:].mean()

# Calcula média e desvio padrão
media = variacao_mensal.mean()
desvio = variacao_mensal.std()

# Define limite (ex: 2 desvios padrão)
limite_superior = media + 2 * desvio
limite_inferior = media - 2 * desvio

# Filtra dados dentro do limite
filtro = variacao_mensal.between(limite_inferior, limite_superior)
df_filtrado = variacao_mensal[filtro]
CRESCIMENTO = round(df_filtrado.mean(),4)

df_final['CRESCIMENTO_GERAL'] = 0.2

CRESCIMENTO


np.float64(0.2164)

In [96]:
df_final.columns[39:54]

Index(['202411', '202412', '202413', '202414', '202501', '202502', '202503',
       '202504', '202505', '202506', '202507', '202508', '202509', '202510',
       '202511'],
      dtype='object')

In [97]:
vendas_todos_historicos = df_final.columns[39:54]

df_final['MEDIANA DO HISTÓRICO'] = df_final[vendas_todos_historicos].median(axis=1)

df_final['MEDIA DO HISTÓRICO'] = df_final[vendas_todos_historicos].mean(axis=1)

medi = df_final.groupby(['CANAL','UF','Código'])['MEDIANA DO HISTÓRICO'].max().reset_index()
medi = medi.rename(columns={'MEDIANA DO HISTÓRICO':'med_por_canal'})

df_final = pd.merge(left=df_final, right=medi,on=['CANAL','UF','Código'],how='left')

medi

CANAL   UF  Código  med_por_canal
0     TODOS   AL   46938            0.0
1     TODOS   AL   47196            0.0
2     TODOS   AL   49899            0.0
3     TODOS   AL   49901            0.0
4     TODOS   AL   49902            0.0
...     ...  ...     ...            ...
1075     VD  VDC   84753            0.0
1076     VD  VDC   84754            1.0
1077     VD  VDC   86115            0.0
1078     VD  VDC   86975            0.0
1079     VD  VDC   87520            0.0

[1080 rows x 4 columns]

In [98]:
df_final.columns[41]

'202413'

In [99]:
mesmo_ciclo_ano_passado = df_final.columns[41]
ciclo_ano_passado = df_final.columns[41]
df_final[ciclo_ano_passado] = df_final[mesmo_ciclo_ano_passado]

In [100]:
'''df_final['CRESCIMENTO_GERAL'] = 0.2
df_final['CRESCIMENTO'] = 0.2'''

"df_final['CRESCIMENTO_GERAL'] = 0.2\ndf_final['CRESCIMENTO'] = 0.2"

In [101]:
df_final['CRESCIMENTO_FINAL'] = df_final['CRESCIMENTO_GERAL'] + df_final['CRESCIMENTO'] #crescimento do pdv

df_final['CRESCIMENTO_FINAL'] = np.where(df_final['CRESCIMENTO_GERAL'] + df_final['CRESCIMENTO']>0.8,0.8,df_final['CRESCIMENTO_GERAL'] + df_final['CRESCIMENTO'])

df_final['CRESCIMENTO_FINAL'] = np.where(df_final['CRESCIMENTO_GERAL'] + df_final['CRESCIMENTO']<0,0,df_final['CRESCIMENTO_GERAL'] + df_final['CRESCIMENTO'])

df_final['MEDIANA DO HISTÓRICO2'] = np.where(df_final['MEDIANA DO HISTÓRICO']==0,df_final['MEDIA DO HISTÓRICO'] ,df_final['MEDIANA DO HISTÓRICO'])

# Primeiro cálculo intermediário
df_final['PV GINSENG'] = np.where(df_final['CRESCIMENTO_FINAL'] * df_final[ciclo_ano_passado] + df_final[ciclo_ano_passado] <round(df_final['CRESCIMENTO_FINAL'] * df_final['MEDIANA DO HISTÓRICO2']+ df_final['MEDIANA DO HISTÓRICO2'],0),
                                    round(df_final['CRESCIMENTO_FINAL'] * df_final['MEDIANA DO HISTÓRICO2']+ df_final['MEDIANA DO HISTÓRICO2'],0), 
                                    round(df_final['CRESCIMENTO_FINAL']*df_final[ciclo_ano_passado]+df_final[ciclo_ano_passado],0))


df_final.shape

(3771, 77)

In [102]:
df_final['PDV'].value_counts()

PDV
20997     117
20970     116
23711     116
20998     115
20993     115
20996     114
21278     113
20969     112
20995     112
20992     112
21383     112
21000     112
21001     112
20994     112
22541     112
20989     111
20999     110
20991     110
21495     110
20986     110
20988     110
21375     110
20968     109
23712     109
23704     108
23703     108
23708     108
24255     108
24257     108
24269     108
24293     108
910173    108
910291    108
23813     108
Name: count, dtype: Int64

In [103]:
df_final.head()

Ciclo_x Região  Canal  Código                      Descrição_x  IAF  \
0   202513    NNE  Todos   47196  QDB MASC CILIO BIG BANG 360 10g  Não   
1   202513    NNE  Todos   47196  QDB MASC CILIO BIG BANG 360 10g  Não   
2   202513    NNE  Todos   47196  QDB MASC CILIO BIG BANG 360 10g  Não   
3   202513    NNE  Todos   47196  QDB MASC CILIO BIG BANG 360 10g  Não   
4   202513    NNE  Todos   47196  QDB MASC CILIO BIG BANG 360 10g  Não   

  Tipo de pedido Foco Unidade de negócio                Marca  ...  \
0       Especial  Sim                QDB  QUEM DISSE BERENICE  ...   
1       Especial  Sim                QDB  QUEM DISSE BERENICE  ...   
2       Especial  Sim                QDB  QUEM DISSE BERENICE  ...   
3       Especial  Sim                QDB  QUEM DISSE BERENICE  ...   
4       Especial  Sim                QDB  QUEM DISSE BERENICE  ...   

  PICO DE VENDAS 2024 Pico Vendas Ultimos 6 ciclos CRESCIMENTO  \
0                 1.0                          1.0      0.7185   
1                 1.0                          1.0      0.6258   
2                 8.0                          8.0      0.7643   
3                 2.0                          1.0      1.6758   
4                 5.0                          1.0      0.2077   

  CRESCIMENTO_GERAL MEDIANA DO HISTÓRICO MEDIA DO HISTÓRICO med_por_canal  \
0               0.2                  0.0           0.133333           0.0   
1               0.2                  0.0           0.066667           0.0   
2               0.2                  0.0           1.133333           4.0   
3               0.2                  0.0           0.266667           0.0   
4               0.2                  0.0           0.600000           0.0   

  CRESCIMENTO_FINAL  MEDIANA DO HISTÓRICO2  PV GINSENG  
0            0.9185               0.133333         0.0  
1            0.8258               0.066667         0.0  
2            0.9643               1.133333         2.0  
3            1.8758               0.266667         6.0  
4            0.4077               0.600000         3.0  

[5 rows x 77 columns]

In [104]:
df_final = df_final.drop(columns=['MEDIANA DO HISTÓRICO2'] )

In [108]:
df_final.columns[49:54]

Index(['C-4', 'C-3', 'C-2', 'C-1', 'Atual'], dtype='object')

In [106]:
df_final = df_final.rename(columns={df_final.columns[49]: "C-4", df_final.columns[50]: "C-3",df_final.columns[51]: "C-2",df_final.columns[52]: "C-1",df_final.columns[53]: "Atual"})

In [110]:
df_final.columns[38:41]

Index(['SKU_FINAL', '202411', '202412'], dtype='object')

In [111]:
df_final.drop(columns=df_final.columns[42:49], inplace=True)
df_final.drop(columns=df_final.columns[38:41], inplace=True)

In [112]:
df_final['COBERTURA ATUAL'] = df_final['ESTOQUE ATUAL'].astype(float) / df_final['DDV PREVISTO'].astype(float)

In [113]:
df_final['COBERTURA ATUAL'] = df_final['COBERTURA ATUAL'].replace([np.inf, -np.inf], 0)

df_final['COBERTURA ATUAL'] = round(df_final['COBERTURA ATUAL'],0)

In [114]:
df_final["DDV PREVISTO"] = df_final["DDV PREVISTO"].astype(float)

df_final["DDV PREVISTO"] = df_final["DDV PREVISTO"].fillna(0)

In [115]:
df_final['PDV'].value_counts()

PDV
20997     117
20970     116
23711     116
20998     115
20993     115
20996     114
21278     113
20969     112
20995     112
20992     112
21383     112
21000     112
21001     112
20994     112
22541     112
20989     111
20999     110
20991     110
21495     110
20986     110
20988     110
21375     110
20968     109
23712     109
23704     108
23703     108
23708     108
24255     108
24257     108
24269     108
24293     108
910173    108
910291    108
23813     108
Name: count, dtype: Int64

In [116]:
r'''colunas_chave = [c for c in df_final.columns if c not in ["DDV PREVISTO", "COBERTURA ATUAL"]]


# encontrar índice da linha com maior DDV e depois maior COBERTURA
idx = (
df_final
.sort_values(["DDV PREVISTO", "COBERTURA ATUAL"], ascending=[False, False])
.groupby(colunas_chave, as_index=False)
.head(1)
)


# reordenar colunas como no original
df_final_dedup = idx[df_final.columns.tolist()].reset_index(drop=True)'''

df_final_dedup = df_final

In [117]:
df_final.columns

Index(['Ciclo_x', 'Região', 'Canal', 'Código', 'Descrição_x', 'IAF',
       'Tipo de pedido', 'Foco', 'Unidade de negócio', 'Marca', 'Categoria',
       'Tipo de promoção', 'Catálogo', 'Tipo de produto', 'Ação consumidor',
       'Percentual de desconto consumidor', 'Ação revendedor',
       'Percentual de desconto revendedor', 'MATCH', 'PDV', 'CANAL',
       'DESCRIÇÃO PDV', 'UF', 'ANALISTA', 'SUPERVISOR', 'SUP', 'ANALISTA EUD',
       'SKU', 'DESCRICAO_x', 'curva', 'categoria', 'proj_mar', 'proj_mar+1',
       'ESTOQUE ATUAL', 'ESTOQUE EM TRANSITO', 'PEDIDO PENDENTE',
       'DDV PREVISTO', 'preço', '202413', 'C-4', 'C-3', 'C-2', 'C-1', 'Atual',
       'INICIO CICLO', 'FIM CICLO', 'DURAÇÃO', 'dias_ate_inicio',
       'Descrição_y', 'chave sku2', 'chave sku1', 'PRECO DE COMPRA',
       'PRECO DE VENDA', 'UFPRODUTO', 'PDV GINSENG', 'PRODUTO', 'chave',
       'PICO DE VENDAS 2024', 'Pico Vendas Ultimos 6 ciclos', 'CRESCIMENTO',
       'CRESCIMENTO_GERAL', 'MEDIANA DO HISTÓRICO', 'MEDIA 

In [118]:
# Columns to bring up front
priority_cols = [
    'SKU',	'Marca',	'INICIO CICLO',
    'FIM CICLO',	'DURAÇÃO',	'PRECO DE COMPRA',	'PRECO DE VENDA',
    'UFPRODUTO',	'Item Desativado',	'Data Prevista Regularização',
    'ANALISTA',	'UF',	'CANAL',	'PDV',	'DESCRIÇÃO PDV',	'Classe',
    'Descrição',	'Categoria',
	'ESTOQUE ATUAL', 'ESTOQUE EM TRANSITO',	'COBERTURA ATUAL',
    'Pedido Pendente',	'PICO DE VENDAS 2024','Pico Vendas Ultimos 6 ciclos',
    'C-4',	'C-3',	'C-2',	'C-1',	'Histórico de Vendas do Ciclo Atual',
    'Dias sem venda'
]

# All remaining columns
other_cols = [col for col in df_final_dedup.columns if col not in priority_cols]

# Reorder
'Ação consumidor', 'Percentual de desconto consumidor', 'Ação revendedor', 'Percentual de desconto revendedor', '202408'


('Ação consumidor',
 'Percentual de desconto consumidor',
 'Ação revendedor',
 'Percentual de desconto revendedor',
 '202408')

In [119]:
df_final_dedup[df_final_dedup['PDV'] == 21007]

Empty DataFrame
Columns: [Ciclo_x, Região, Canal, Código, Descrição_x, IAF, Tipo de pedido, Foco, Unidade de negócio, Marca, Categoria, Tipo de promoção, Catálogo, Tipo de produto, Ação consumidor, Percentual de desconto consumidor, Ação revendedor, Percentual de desconto revendedor, MATCH, PDV, CANAL, DESCRIÇÃO PDV, UF, ANALISTA, SUPERVISOR, SUP, ANALISTA EUD, SKU, DESCRICAO_x, curva, categoria, proj_mar, proj_mar+1, ESTOQUE ATUAL, ESTOQUE EM TRANSITO, PEDIDO PENDENTE, DDV PREVISTO, preço, 202413, C-4, C-3, C-2, C-1, Atual, INICIO CICLO, FIM CICLO, DURAÇÃO, dias_ate_inicio, Descrição_y, chave sku2, chave sku1, PRECO DE COMPRA, PRECO DE VENDA, UFPRODUTO, PDV GINSENG, PRODUTO, chave, PICO DE VENDAS 2024, Pico Vendas Ultimos 6 ciclos, CRESCIMENTO, CRESCIMENTO_GERAL, MEDIANA DO HISTÓRICO, MEDIA DO HISTÓRICO, med_por_canal, CRESCIMENTO_FINAL, PV GINSENG, COBERTURA ATUAL]
Index: []

[0 rows x 67 columns]

In [120]:
df_final_dedup.drop(columns=['dias_ate_inicio', 'CRESCIMENTO'],inplace=True)

In [121]:
df_final_dedup['INICIO CICLO'] = pd.to_datetime(df_final_dedup['INICIO CICLO'], dayfirst=True).dt.strftime('%d/%m/%Y')

df_final_dedup['FIM CICLO'] = pd.to_datetime(df_final_dedup['FIM CICLO'], dayfirst=True).dt.strftime('%d/%m/%Y')

In [122]:
df_final_dedup['Percentual de desconto revendedor'] = np.where((df_final_dedup['Percentual de desconto revendedor'].isna()) & (~df_final_dedup['Percentual de desconto consumidor'].isna()),df_final_dedup['Percentual de desconto consumidor'],df_final_dedup['Percentual de desconto revendedor'])

In [123]:
df_pdv_origi['PDV'] = df_pdv_origi['PDV'].astype('Int64')
df_final_dedup['PDV'] = df_final_dedup['PDV'].astype('Int64')


df_final_dedup = pd.merge(left=df_final_dedup,right=df_pdv_origi[['PDV','CANAL','UF']],how='left',on='PDV')

In [124]:
df_final_dedup['Código'].isna().sum()

np.int64(0)

In [125]:
df_irece_agrupado = df_irece.groupby(['PDV','Código','Ciclo'])['Quantidade'].sum().reset_index()

In [126]:
df_final_dedup = df_final_dedup.rename(columns={'CANAL_x':'CANAL','UF_X':'UF','Marca':'LINHA'})


In [127]:
df_final_dedup['PDV'].value_counts()

PDV
20997     117
20970     116
23711     116
20998     115
20993     115
20996     114
21278     113
20969     112
20995     112
20992     112
21383     112
21000     112
21001     112
20994     112
22541     112
20989     111
20999     110
20991     110
21495     110
20986     110
20988     110
21375     110
20968     109
23712     109
23704     108
23703     108
23708     108
24255     108
24257     108
24269     108
24293     108
910173    108
910291    108
23813     108
Name: count, dtype: Int64

In [128]:
df_final_dedup = df_final_dedup.rename(columns={'UF_x':'UF','DESCRICAO_y':'DESCRICAO'})

In [129]:
df_final_dedup = df_final_dedup.drop(columns={'CANAL_y', 'UF_y'})


In [130]:
df_final_dedup['Estoque Total'] = df_final_dedup['ESTOQUE ATUAL'].astype(float) + df_final_dedup['ESTOQUE EM TRANSITO'].astype(float) + df_final_dedup['PEDIDO PENDENTE'].astype(float)

In [131]:
ciclo_ano_passado

'202413'

In [132]:
df_final_dedup = df_final_dedup.drop(columns='Descrição_y')

df_final_dedup = df_final_dedup.rename(columns={'Descrição_x':'Descrição'})

In [133]:
df_final_dedup.columns

Index(['Ciclo_x', 'Região', 'Canal', 'Código', 'Descrição', 'IAF',
       'Tipo de pedido', 'Foco', 'Unidade de negócio', 'LINHA', 'Categoria',
       'Tipo de promoção', 'Catálogo', 'Tipo de produto', 'Ação consumidor',
       'Percentual de desconto consumidor', 'Ação revendedor',
       'Percentual de desconto revendedor', 'MATCH', 'PDV', 'CANAL',
       'DESCRIÇÃO PDV', 'UF', 'ANALISTA', 'SUPERVISOR', 'SUP', 'ANALISTA EUD',
       'SKU', 'DESCRICAO_x', 'curva', 'categoria', 'proj_mar', 'proj_mar+1',
       'ESTOQUE ATUAL', 'ESTOQUE EM TRANSITO', 'PEDIDO PENDENTE',
       'DDV PREVISTO', 'preço', '202413', 'C-4', 'C-3', 'C-2', 'C-1', 'Atual',
       'INICIO CICLO', 'FIM CICLO', 'DURAÇÃO', 'chave sku2', 'chave sku1',
       'PRECO DE COMPRA', 'PRECO DE VENDA', 'UFPRODUTO', 'PDV GINSENG',
       'PRODUTO', 'chave', 'PICO DE VENDAS 2024',
       'Pico Vendas Ultimos 6 ciclos', 'CRESCIMENTO_GERAL',
       'MEDIANA DO HISTÓRICO', 'MEDIA DO HISTÓRICO', 'med_por_canal',
       'CRESCIMENTO

In [134]:
# colunas de agrupamento
cols_group = [
'CANAL','ANALISTA','SUPERVISOR','UF','chave','PDV','DESCRIÇÃO PDV','Código','Descrição','LINHA','Categoria'
]


# colunas para somar
cols_sum = [
'ESTOQUE ATUAL','ESTOQUE EM TRANSITO','PEDIDO PENDENTE','Estoque Total','DDV PREVISTO'
]


# construir dicionário de agregação
agg_dict = {}
for col in df_final_dedup.columns:
    if col in cols_group:
        continue
    elif col in cols_sum:
        agg_dict[col] = 'sum'
    else:
        agg_dict[col] = 'max'

# aplicar groupby
result = df_final_dedup.groupby(cols_group, as_index=False).agg(agg_dict)

In [135]:
df_final_dedup = result

In [136]:
df_final_dedup = df_final_dedup[['DURAÇÃO','CANAL','ANALISTA','SUPERVISOR','UF','chave','PDV','DESCRIÇÃO PDV','Código','Descrição','LINHA','Categoria','curva','Percentual de desconto consumidor','Ação consumidor',
                                 'Percentual de desconto revendedor','Ação revendedor','C-4', 'C-3', 'C-2', 'C-1','Atual',ciclo_ano_passado ,'ESTOQUE ATUAL','ESTOQUE EM TRANSITO','PEDIDO PENDENTE','Estoque Total',
                                 'DDV PREVISTO','COBERTURA ATUAL','proj_mar', 'proj_mar+1','MEDIA DO HISTÓRICO','PICO DE VENDAS 2024','Pico Vendas Ultimos 6 ciclos','PRECO DE COMPRA',
                                'PRECO DE VENDA','PV GINSENG']]

In [137]:
df_final_dedup['Percentual de desconto revendedor'] = np.where(df_final_dedup['Percentual de desconto revendedor'] == '0,00', df_final_dedup['Percentual de desconto consumidor'],df_final_dedup['Percentual de desconto revendedor'])

C:\Users\joao.herculano\AppData\Local\Temp\ipykernel_43676\3244855783.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_final_dedup['Percentual de desconto revendedor'] = np.where(df_final_dedup['Percentual de desconto revendedor'] == '0,00', df_final_dedup['Percentual de desconto consumidor'],df_final_dedup['Percentual de desconto revendedor'])


In [138]:
ciclo_ano_passado

'202413'

In [139]:
df_final_dedup = df_final_dedup.drop_duplicates()

In [140]:
df_final_dedup['Valor Sugestão'] = ""

df_final_dedup['Sugestão Abastecimento'] = ""

In [141]:
df_final_dedup[['DDV PREVISTO',
       'COBERTURA ATUAL',]].dtypes

DDV PREVISTO       float64
COBERTURA ATUAL    float64
dtype: object

In [142]:
df_final_dedup[ 'DDV PREVISTO'] =  df_final_dedup['DDV PREVISTO'].fillna(0)

df_final_dedup = df_final_dedup.drop_duplicates()

In [143]:
df_final_dedup[df_final_dedup['chave'] == '2371184387']['DDV PREVISTO'].head()


Series([], Name: DDV PREVISTO, dtype: float64)

In [144]:
df_final_dedup['PDV'].value_counts()

PDV
20988     108
21000     108
21375     108
910173    108
910291    108
21495     108
23708     108
20986     108
21001     108
23712     108
20989     108
20999     108
23813     108
24293     108
20968     108
20969     108
20991     108
24257     108
20970     108
20993     108
21383     108
20996     108
22541     108
20992     108
21278     108
24269     108
24255     108
23703     108
20997     108
20994     108
23704     108
20995     108
20998     108
23711     108
Name: count, dtype: Int64

In [145]:
df_pdv_origi['PDV'] = df_pdv_origi['PDV'].astype('Int64')



df_pdv_origi = df_pdv_origi.rename(columns={'CANAL':'CANAL_CERTO'})

df_final_dedup= pd.merge(df_final_dedup,df_pdv_origi[['PDV','CANAL_CERTO']],on='PDV',how='inner')

df_final_dedup['CANAL']= df_final_dedup['CANAL_CERTO']


df_final_dedup.columns

Index(['DURAÇÃO', 'CANAL', 'ANALISTA', 'SUPERVISOR', 'UF', 'chave', 'PDV',
       'DESCRIÇÃO PDV', 'Código', 'Descrição', 'LINHA', 'Categoria', 'curva',
       'Percentual de desconto consumidor', 'Ação consumidor',
       'Percentual de desconto revendedor', 'Ação revendedor', 'C-4', 'C-3',
       'C-2', 'C-1', 'Atual', '202413', 'ESTOQUE ATUAL', 'ESTOQUE EM TRANSITO',
       'PEDIDO PENDENTE', 'Estoque Total', 'DDV PREVISTO', 'COBERTURA ATUAL',
       'proj_mar', 'proj_mar+1', 'MEDIA DO HISTÓRICO', 'PICO DE VENDAS 2024',
       'Pico Vendas Ultimos 6 ciclos', 'PRECO DE COMPRA', 'PRECO DE VENDA',
       'PV GINSENG', 'Valor Sugestão', 'Sugestão Abastecimento',
       'CANAL_CERTO'],
      dtype='object')

In [146]:
df_final_dedup=df_final_dedup.drop(columns=['CANAL_CERTO'])

In [147]:
df_final_dedup['PDV'].value_counts()

PDV
20988     108
21000     108
21375     108
910173    108
910291    108
21495     108
23708     108
20986     108
21001     108
23712     108
20989     108
20999     108
23813     108
24293     108
20968     108
20969     108
20991     108
24257     108
20970     108
20993     108
21383     108
20996     108
22541     108
20992     108
21278     108
24269     108
24255     108
23703     108
20997     108
20994     108
23704     108
20995     108
20998     108
23711     108
Name: count, dtype: Int64

In [148]:
# Export to Excel
output_file = f'C:\\Users\\joao.herculano\\Documents\\promoção_QDB_{ciclo_mais2}.{hoje}.xlsx'
with pd.ExcelWriter(output_file, engine='openpyxl') as writer:
    df_final_dedup.to_excel(writer, index=False)

# Apply styles
wb = load_workbook(output_file)
ws = wb['Sheet1']

# Style header
header_fill = PatternFill(start_color='ADD8E6', end_color='ADD8E6', fill_type='solid')  # Light Blue
header_font = Font(color='FFFFFF', bold=True)  # White & Bold

for cell in ws[1]:
    cell.fill = header_fill
    cell.font = header_font

# Style rows: gray/white alternating
gray_fill = PatternFill(start_color='DDDDDD', end_color='DDDDDD', fill_type='solid')  # Light gray

for i, row in enumerate(ws.iter_rows(min_row=2, max_row=ws.max_row), start=2):
    if i % 2 == 0:
        for cell in row:
            cell.fill = gray_fill

# Save styled workbook
wb.save(output_file)


coisas q saem

Lançamento
Subcategoria
Projeção Próximo Ciclo 
Promoção Próximo Ciclo
Compra inteligente semanal/Sugestão de compra
Compra inteligente Próximo Ciclo
Planograma
Carteira Bloqueada Para Novos Pedidos
Quantidade por caixa
Preço Sell In
Quantidade
Item analisado
Tipo Preço

>>>>>>>>>>>>>NAO ESTÁ PEGANDO O MERGE COM O DF_ESTOQUE


CRIAR PROJEÇÃO DE VENDA DO CICLO ATUAL
Compra inteligente Próximo Ciclo + 1 >>>>>>> RENAME PRA NOROMAL